# Using Evolutionary Algorithms in DESDEO

Here, we will show multiple ways of using Evolutionary Algorithms (EAs) in DESDEO, depending on the user's needs. Be sure to read the explanation on [how these algorithms are structured](../explanation/templates_and_pub_sub.md). We will showcase three different ways of using EAs in DESDEO:
- Using inbuilt algorithms in DESDEO for to calculate a representative set of solutions for multi-objective optimization problems.
- Using inbuilt algorithms in DESDEO for to interactive evolutionary multi-objective optimization.
- Using components implemented in DESDEO to build custom EAs (interactive or not).

## Using inbuilt algorithms in DESDEO

First, let's import the necessary classes and functions from DESDEO.

In [3]:
import plotly.graph_objects as go

from desdeo.emo.hooks.archivers import NonDominatedArchive
from desdeo.emo.methods.EAs import nsga3, rvea
from desdeo.problem.testproblems import dtlz2

First, we instantiate the problem we want to solve. We will use the `DTLZ2` problem from the `desdeo.problems` module.

Then, we will pass the problem to the `nsga3` method from the desdeo.emo module. This method creates a solver and a publisher object. The solver object can be run to solve the problem using NSGA-III, while the publisher object can be used to append additional components to the algorithm. We will see the usage of publisher further down.

In [5]:
problem = dtlz2(n_variables=10, n_objectives=3)

solver, publisher = nsga3(problem=problem)

result = solver()

Running the solver object will return a `EMOResult` object, which contains the final population of solutions.

In [22]:
print(result.solutions.head())  # Contains the decision variables values

print(result.outputs.head())  # Contains the objective values, target values (values that are minimized), and constraints, and extra functions.


shape: (5, 10)
┌──────────┬──────────┬──────────┬──────────┬───┬──────────┬──────────┬──────────┬──────────┐
│ x_1      ┆ x_2      ┆ x_3      ┆ x_4      ┆ … ┆ x_7      ┆ x_8      ┆ x_9      ┆ x_10     │
│ ---      ┆ ---      ┆ ---      ┆ ---      ┆   ┆ ---      ┆ ---      ┆ ---      ┆ ---      │
│ f64      ┆ f64      ┆ f64      ┆ f64      ┆   ┆ f64      ┆ f64      ┆ f64      ┆ f64      │
╞══════════╪══════════╪══════════╪══════════╪═══╪══════════╪══════════╪══════════╪══════════╡
│ 0.172399 ┆ 0.941215 ┆ 0.526616 ┆ 0.503834 ┆ … ┆ 0.51059  ┆ 0.501721 ┆ 0.489547 ┆ 0.510606 │
│ 0.364355 ┆ 0.068903 ┆ 0.503061 ┆ 0.487    ┆ … ┆ 0.515685 ┆ 0.520767 ┆ 0.487931 ┆ 0.498902 │
│ 0.510864 ┆ 0.681579 ┆ 0.523908 ┆ 0.50026  ┆ … ┆ 0.493216 ┆ 0.500725 ┆ 0.521979 ┆ 0.526014 │
│ 0.296107 ┆ 0.0      ┆ 0.527449 ┆ 0.500501 ┆ … ┆ 0.529618 ┆ 0.497065 ┆ 0.492248 ┆ 0.499054 │
│ 0.520778 ┆ 0.045575 ┆ 0.504395 ┆ 0.478581 ┆ … ┆ 0.538859 ┆ 0.495535 ┆ 0.520674 ┆ 0.501883 │
└──────────┴──────────┴──────────┴──────────┴

In [29]:
go.Figure(
    go.Scatter3d(
        x=result.outputs["f_1"],
        y=result.outputs["f_2"],
        z=result.outputs["f_3"],
        mode="markers",
        marker=dict(size=2),
    )
)

Note that the results object only contains the final population of the EA.
Many users will instead want to keep an archive of solutions and use that for further analysis.
We provide many different kinds of archivers that can hook into the evolutionary process.
One such archiver is the `NonDominatedArchive` which keeps track of the non-dominated solutions found during the evolutionary process.

To use it, simply make sure that the archive is registered with the publisher. Do note that as this archive will be updated every generation,
it will run non-dominatation checks many times, slowing down the process a bit. We will provide a more efficient archiver in the future.

In [24]:
problem = dtlz2(n_variables=10, n_objectives=3)

solver, publisher = nsga3(problem=problem)

archive = NonDominatedArchive(problem=problem, publisher=publisher)
publisher.auto_subscribe(archive)

results = solver()

In [ ]:
# Lets plot the results. As we can see, using an archive, we get a much denser representation of the Pareto front using the same number of function evaluations.

go.Figure(
    go.Scatter3d(
        x=archive.archive["f_1"],
        y=archive.archive["f_2"],
        z=archive.archive["f_3"],
        mode="markers",
        marker=dict(size=2),
    )
)

## Using inbuilt algorithms in DESDEO for interactive evolutionary multi-objective optimization

Now, we will showcase how the inbuilt algorithms in DESDEO can be used for interactive evolutionary multi-objective optimization. We will also showcase how to change some default parameters of the algorithm.

In [ ]:
problem = dtlz2(n_variables=10, n_objectives=3)

reference_point = {  # This allows you to specify a reference point for the algorithm to use.
    "f_1_min": 0.5,
    "f_2_min": 0.5,
    "f_3_min": 0.5}  # Note that these are target symbols, not objective symbols

solver, publisher = nsga3(
    problem=problem,
    reference_vector_options={  # This argument can be used to change how reference vectors are generated.
        "reference_point": reference_point,
        "interactive_adaptation": "reference_point",
        "number_of_vectors": 30,
        # Note: due to the way the reference vectors are generated,
        # this number is not guaranteed to be the number of reference vectors used.
        # But it is a good estimate.
        })

results = solver()

In [17]:
# Let us plot the results
go.Figure(
    go.Scatter3d(
        x=results.outputs["f_1"],
        y=results.outputs["f_2"],
        z=results.outputs["f_3"],
        mode="markers",
        marker=dict(size=2),
    )
)

To run multiple iterations, simply reinitalize the solver object with new preferences.
Currently, the solver restarts at each new iteration, "forgetting" the previous solutions.
We will provide a way to keep the previous solutions in the future.

Let's try a different preference format for the second iteration.

In [31]:
problem = dtlz2(n_variables=10, n_objectives=3)

preferred_solutions = {  # This allows you to specify multiple regions of interest.
    "f_1_min": [0.5, 0.1, 0.9],
    "f_2_min": [0.5, 0.1, 0.4],
    "f_3_min": [0.5, 0.9, 0.3]}  # Note that these are target symbols, not objective symbols

solver, publisher = nsga3(
    problem=problem,
    reference_vector_options={  # This argument can be used to change how reference vectors are generated.
        "preferred_solutions": preferred_solutions,
        "interactive_adaptation": "preferred_solutions",
        "number_of_vectors": 30,
        # Note: due to the way the reference vectors are generated,
        # this number is not guaranteed to be the number of reference vectors used.
        # But it is a good estimate.
        })

results = solver()

In [33]:
# Let us plot the results
fig = go.Figure(
    go.Scatter3d(
        x=results.outputs["f_1"],
        y=results.outputs["f_2"],
        z=results.outputs["f_3"],
        mode="markers",
        marker=dict(size=2),
        name="solutions"
    )
)

fig.add_trace(
    go.Scatter3d(
        x=preferred_solutions["f_1_min"],
        y=preferred_solutions["f_2_min"],
        z=preferred_solutions["f_3_min"],
        mode="markers",
        marker=dict(size=10),
        name="preference",
    )
)

Note that the solutions are not symmetrically distributed around the provided reference points.
This is due to how the interactive algorithm works, and is not a bug. There are a few other ways to provide preferences, which we will showcase in the next sections.

## Using components implemented in DESDEO to build custom EAs

Finally, we will showcase how to build custom EAs using components implemented in DESDEO. We will use the `rvea` algorithm as an example.

First, we import the necessary components from DESDEO.

In [1]:
from desdeo.emo.hooks.archivers import Archive
from desdeo.emo.methods.bases import template1
from desdeo.emo.operators.crossover import SimulatedBinaryCrossover
from desdeo.emo.operators.evaluator import EMOEvaluator
from desdeo.emo.operators.generator import RandomGenerator
from desdeo.emo.operators.mutation import BoundedPolynomialMutation
from desdeo.emo.operators.selection import (
    NSGAIII_select,
    ParameterAdaptationStrategy,
    ReferenceVectorOptions,
    RVEASelector,
)
from desdeo.emo.operators.termination import MaxEvaluationsTerminator
from desdeo.tools.patterns import Publisher


d:\Projects\DESDEO\.venv\Lib\site-packages\pydantic\_internal\_config.py:341: UserWarning: Valid config keys have changed in V2:
* 'allow_population_by_field_name' has been renamed to 'populate_by_name'
  warnings.warn(message, UserWarning)


In [ ]:
# Initialize a publisher
publisher = Publisher()
seed = 0

# Initialize EA components

# EMOEvaluator is used to evaluate the solutions
evaluator = EMOEvaluator(
    problem=problem,
    publisher=publisher,
    verbosity=2
)

# RVEASelector is the selection operator for RVEA
preferred_ranges = {
        "f_1_min": [0.1, 0.6],
        "f_2_min": [0.2, 0.7],
        "f_3_min": [0.3, 0.6],
    }
reference_vector_options = ReferenceVectorOptions(
    interactive_adaptation="preferred_ranges",
    preferred_ranges=preferred_ranges,
    number_of_vectors=30,
)

selector = RVEASelector(
    problem=problem,
    publisher=publisher,
    reference_vector_options=reference_vector_options,
    verbosity=2,
    parameter_adaptation_strategy=ParameterAdaptationStrategy.FUNCTION_EVALUATION_BASED
)

# Note that the initial population size is equal to the number of reference vectors
n_points = selector.reference_vectors.shape[0]

# RandomGenerator is used to generate the initial population. Other generators can be used as well.
generator = RandomGenerator(
    problem=problem,
    evaluator=evaluator,
    publisher=publisher,
    n_points=n_points,
    seed=seed,
    verbosity=1,
)

# SimulatedBinaryCrossover is the crossover operator for RVEA
crossover = SimulatedBinaryCrossover(
problem=problem,
publisher=publisher,
seed=seed,
verbosity=1,
)

# BoundedPolynomialMutation is the mutation operator for RVEA
mutation = BoundedPolynomialMutation(
problem=problem,
publisher=publisher,
seed=seed,
verbosity=1,
)

# MaxEvaluationsTerminator ends the optimization after a certain number of evaluations
# Actually, it stops the optimization 1 generation _after_ the number of evaluations has been reached.
# This is annoying, but it is a limitation of the current implementation.
# A temporary workaround is to set the number of evaluations to a number that less than the desired number of
# evaluations by the number of reference vectors.
terminator = MaxEvaluationsTerminator(max_evaluations=50000, publisher=publisher)

# Register the components to the publisher
components = [evaluator, generator, crossover, mutation, selector, terminator]
[publisher.auto_subscribe(x) for x in components]
[publisher.register_topics(x.provided_topics[x.verbosity], x.__class__.__name__) for x in components]

# Choose a template for the EA. template1 is a basic EA template.
results = template1(
    crossover=crossover,
    mutation=mutation,
    selection=selector,
    generator=generator,
    terminator=terminator,
    evaluator=evaluator,
)

D:\Projects\DESDEO\desdeo\emo\operators\selection.py:665: RuntimeWarning:

invalid value encountered in arccos

D:\Projects\DESDEO\desdeo\emo\operators\selection.py:553: RuntimeWarning:

All-NaN slice encountered



In [62]:
# Let us plot the results
fig = go.Figure(
    go.Scatter3d(
        x=results.outputs["f_1"],
        y=results.outputs["f_2"],
        z=results.outputs["f_3"],
        mode="markers",
        marker=dict(size=2),
    )
)

# calculate all corners of the bounding box of the preferred ranges

corners = [
    [preferred_ranges["f_1_min"][0], preferred_ranges["f_2_min"][0], preferred_ranges["f_3_min"][0]],
    [preferred_ranges["f_1_min"][0], preferred_ranges["f_2_min"][0], preferred_ranges["f_3_min"][1]],
    [preferred_ranges["f_1_min"][0], preferred_ranges["f_2_min"][1], preferred_ranges["f_3_min"][0]],
    [preferred_ranges["f_1_min"][0], preferred_ranges["f_2_min"][1], preferred_ranges["f_3_min"][1]],
    [preferred_ranges["f_1_min"][1], preferred_ranges["f_2_min"][0], preferred_ranges["f_3_min"][0]],
    [preferred_ranges["f_1_min"][1], preferred_ranges["f_2_min"][0], preferred_ranges["f_3_min"][1]],
    [preferred_ranges["f_1_min"][1], preferred_ranges["f_2_min"][1], preferred_ranges["f_3_min"][0]],
    [preferred_ranges["f_1_min"][1], preferred_ranges["f_2_min"][1], preferred_ranges["f_3_min"][1]],
]

# plot the corners
fig.add_trace(
    go.Scatter3d(
        x=[x[0] for x in corners],
        y=[x[1] for x in corners],
        z=[x[2] for x in corners],
        mode="markers+lines",
        marker=dict(size=3),
        name="preference",
    )
)

Finally, let us try the remaining way of conducting optimization, this time using NSGA-3.
We will use the "non-preferred solution" to define regions of disinterest.

We will also try keeping an archive of all found solutions.

In [10]:
# Initialize a publisher
publisher = Publisher()
seed = 0
problem = dtlz2(n_variables=10, n_objectives=3)

# Initialize EA components

# EMOEvaluator is used to evaluate the solutions
evaluator = EMOEvaluator(
    problem=problem,
    publisher=publisher,
    verbosity=2
)

# RVEASelector is the selection operator for RVEA
non_preferred_solutions = {
        "f_1_min": [0.5, 0.1, 0.9],
        "f_2_min": [0.1, 0.9, 0.4],
        "f_3_min": [0.9, 0.3, 0.1],
    }
reference_vector_options = ReferenceVectorOptions(
    interactive_adaptation="non_preferred_solutions",
    non_preferred_solutions=non_preferred_solutions,
)

selector = NSGAIII_select(
    problem=problem,
    publisher=publisher,
    reference_vector_options=reference_vector_options,
    verbosity=2,
)

# Note that the initial population size is equal to the number of reference vectors
n_points = selector.reference_vectors.shape[0]

# RandomGenerator is used to generate the initial population. Other generators can be used as well.
generator = RandomGenerator(
    problem=problem,
    evaluator=evaluator,
    publisher=publisher,
    n_points=n_points,
    seed=seed,
    verbosity=1,
)

# SimulatedBinaryCrossover is the crossover operator for RVEA
crossover = SimulatedBinaryCrossover(
problem=problem,
publisher=publisher,
seed=seed,
verbosity=1,
)

# BoundedPolynomialMutation is the mutation operator for RVEA
mutation = BoundedPolynomialMutation(
problem=problem,
publisher=publisher,
seed=seed,
verbosity=1,
)

# MaxEvaluationsTerminator ends the optimization after a certain number of evaluations
# Actually, it stops the optimization 1 generation _after_ the number of evaluations has been reached.
# This is annoying, but it is a limitation of the current implementation.
# A temporary workaround is to set the number of evaluations to a number that less than the desired number of
# evaluations by the number of reference vectors.
terminator = MaxEvaluationsTerminator(max_evaluations=50000, publisher=publisher)

# Register the components to the publisher
components = [evaluator, generator, crossover, mutation, selector, terminator]
[publisher.auto_subscribe(x) for x in components]
[publisher.register_topics(x.provided_topics[x.verbosity], x.__class__.__name__) for x in components]

# Initialize and register any additional components
archive = Archive(problem=problem, publisher=publisher)
publisher.auto_subscribe(archive)

# Choose a template for the EA. template1 is a basic EA template.
results = template1(
    crossover=crossover,
    mutation=mutation,
    selection=selector,
    generator=generator,
    terminator=terminator,
    evaluator=evaluator,
)

In [11]:
# Let us plot the results

fig = go.Figure(
    go.Scatter3d(
        x=results.outputs["f_1"],
        y=results.outputs["f_2"],
        z=results.outputs["f_3"],
        mode="markers",
        marker=dict(size=2),
    )
)

fig.add_trace(
    go.Scatter3d(
        x=non_preferred_solutions["f_1_min"],
        y=non_preferred_solutions["f_2_min"],
        z=non_preferred_solutions["f_3_min"],
        mode="markers",
        marker=dict(size=10),
        name="non-preference",
    )
)
fig

In [13]:
# Let us plot the archive

fig = go.Figure(
    go.Scatter3d(
        x=archive.archive["f_1"],
        y=archive.archive["f_2"],
        z=archive.archive["f_3"],
        mode="markers",
        marker=dict(size=2),
    )
)

fig